Lambda School Data Science

*Unit 2, Sprint 1, Module 3*

---

# Ridge Regression

## Assignment

We're going back to our other **New York City** real estate dataset. Instead of predicting apartment rents, you'll predict property sales prices.

But not just for condos in Tribeca...

- [ ] Use a subset of the data where `BUILDING_CLASS_CATEGORY` == `'01 ONE FAMILY DWELLINGS'` and the sale price was more than 100 thousand and less than 2 million.
- [ ] Do train/test split. Use data from January — March 2019 to train. Use data from April 2019 to test.
- [ ] Do one-hot encoding of categorical features.
- [ ] Do feature selection with `SelectKBest`.
- [ ] Fit a ridge regression model with multiple features. Use the `normalize=True` parameter (or do [feature scaling](https://scikit-learn.org/stable/modules/preprocessing.html) beforehand — use the scaler's `fit_transform` method with the train set, and the scaler's `transform` method with the test set)
- [ ] Get mean absolute error for the test set.
- [ ] As always, commit your notebook to your fork of the GitHub repo.

The [NYC Department of Finance](https://www1.nyc.gov/site/finance/taxes/property-rolling-sales-data.page) has a glossary of property sales terms and NYC Building Class Code Descriptions. The data comes from the [NYC OpenData](https://data.cityofnewyork.us/browse?q=NYC%20calendar%20sales) portal.


## Stretch Goals

Don't worry, you aren't expected to do all these stretch goals! These are just ideas to consider and choose from.

- [ ] Add your own stretch goal(s) !
- [ ] Instead of `Ridge`, try `LinearRegression`. Depending on how many features you select, your errors will probably blow up! 💥
- [ ] Instead of `Ridge`, try [`RidgeCV`](https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.RidgeCV.html).
- [ ] Learn more about feature selection:
    - ["Permutation importance"](https://www.kaggle.com/dansbecker/permutation-importance)
    - [scikit-learn's User Guide for Feature Selection](https://scikit-learn.org/stable/modules/feature_selection.html)
    - [mlxtend](http://rasbt.github.io/mlxtend/) library
    - scikit-learn-contrib libraries: [boruta_py](https://github.com/scikit-learn-contrib/boruta_py) & [stability-selection](https://github.com/scikit-learn-contrib/stability-selection)
    - [_Feature Engineering and Selection_](http://www.feat.engineering/) by Kuhn & Johnson.
- [ ] Try [statsmodels](https://www.statsmodels.org/stable/index.html) if you’re interested in more inferential statistical approach to linear regression and feature selection, looking at p values and 95% confidence intervals for the coefficients.
- [ ] Read [_An Introduction to Statistical Learning_](http://faculty.marshall.usc.edu/gareth-james/ISL/ISLR%20Seventh%20Printing.pdf), Chapters 1-3, for more math & theory, but in an accessible, readable way.
- [ ] Try [scikit-learn pipelines](https://scikit-learn.org/stable/modules/compose.html).

In [1]:
%%capture
import sys

# If you're on Colab:
if 'google.colab' in sys.modules:
    DATA_PATH = 'https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Applied-Modeling/master/data/'
    !pip install category_encoders==2.*

# If you're working locally:
else:
    DATA_PATH = '../data/'
    
# Ignore this Numpy warning when using Plotly Express:
# FutureWarning: Method .ptp is deprecated and will be removed in a future version. Use numpy.ptp instead.
import warnings
warnings.filterwarnings(action='ignore', category=FutureWarning, module='numpy')

In [2]:
import pandas as pd
import pandas_profiling

# Read New York City property sales data
df = pd.read_csv(DATA_PATH+'condos/NYC_Citywide_Rolling_Calendar_Sales.csv')

# Change column names: replace spaces with underscores
df.columns = [col.replace(' ', '_') for col in df]

# SALE_PRICE was read as strings.
# Remove symbols, convert to integer
df['SALE_PRICE'] = (
    df['SALE_PRICE']
    .str.replace('$','')
    .str.replace('-','')
    .str.replace(',','')
    .astype(int)
)

In [3]:
# BOROUGH is a numeric column, but arguably should be a categorical feature,
# so convert it from a number to a string
df['BOROUGH'] = df['BOROUGH'].astype(str)

In [4]:
# Reduce cardinality for NEIGHBORHOOD feature

# Get a list of the top 10 neighborhoods
top10 = df['NEIGHBORHOOD'].value_counts()[:10].index

# At locations where the neighborhood is NOT in the top 10, 
# replace the neighborhood with 'OTHER'
df.loc[~df['NEIGHBORHOOD'].isin(top10), 'NEIGHBORHOOD'] = 'OTHER'

In [5]:
df["BUILDING_CLASS_CATEGORY"].unique()

array(['13 CONDOS - ELEVATOR APARTMENTS', '21 OFFICE BUILDINGS',
       '15 CONDOS - 2-10 UNIT RESIDENTIAL',
       '07 RENTALS - WALKUP APARTMENTS', '01 ONE FAMILY DWELLINGS',
       '02 TWO FAMILY DWELLINGS', '05 TAX CLASS 1 VACANT LAND',
       '29 COMMERCIAL GARAGES', '32 HOSPITAL AND HEALTH FACILITIES',
       '33 EDUCATIONAL FACILITIES', '08 RENTALS - ELEVATOR APARTMENTS',
       '31 COMMERCIAL VACANT LAND', '41 TAX CLASS 4 - OTHER',
       '14 RENTALS - 4-10 UNIT', '03 THREE FAMILY DWELLINGS',
       '22 STORE BUILDINGS', '10 COOPS - ELEVATOR APARTMENTS',
       '44 CONDO PARKING', '47 CONDO NON-BUSINESS STORAGE',
       '12 CONDOS - WALKUP APARTMENTS', '43 CONDO OFFICE BUILDINGS',
       '09 COOPS - WALKUP APARTMENTS', '27 FACTORIES',
       '04 TAX CLASS 1 CONDOS', '17 CONDO COOPS', '26 OTHER HOTELS',
       '45 CONDO HOTELS', '06 TAX CLASS 1 - OTHER', '30 WAREHOUSES',
       '46 CONDO STORE BUILDINGS', '25 LUXURY HOTELS', '34 THEATRES',
       '37 RELIGIOUS FACILITIES', '49 C

In [6]:
data = df[df["BUILDING_CLASS_CATEGORY"] == '01 ONE FAMILY DWELLINGS']

In [7]:
data = data.loc[(data["SALE_PRICE"] > 100000) & (data["SALE_PRICE"] < 2000000)]

In [8]:
print(data.shape)
data.head()

(3151, 21)


BOROUGH NEIGHBORHOOD  BUILDING_CLASS_CATEGORY TAX_CLASS_AT_PRESENT  BLOCK  \
44        3        OTHER  01 ONE FAMILY DWELLINGS                    1   5495   
61        4        OTHER  01 ONE FAMILY DWELLINGS                    1   7918   
78        2        OTHER  01 ONE FAMILY DWELLINGS                    1   4210   
108       3        OTHER  01 ONE FAMILY DWELLINGS                    1   5212   
111       3        OTHER  01 ONE FAMILY DWELLINGS                    1   7930   

     LOT  EASE-MENT BUILDING_CLASS_AT_PRESENT               ADDRESS  \
44   801        NaN                        A9      4832 BAY PARKWAY   
61    72        NaN                        A1    80-23 232ND STREET   
78    19        NaN                        A1  1260 RHINELANDER AVE   
108   69        NaN                        A1         469 E 25TH ST   
111  121        NaN                        A5      5521 WHITTY LANE   

    APARTMENT_NUMBER  ...  RESIDENTIAL_UNITS  COMMERCIAL_UNITS  TOTAL_UNITS  \
44               NaN  ...                1.0               0.0          1.0   
61               NaN  ...                1.0               0.0          1.0   
78               NaN  ...                1.0               0.0          1.0   
108              NaN  ...                1.0               0.0          1.0   
111              NaN  ...                1.0               0.0          1.0   

     LAND_SQUARE_FEET GROSS_SQUARE_FEET  YEAR_BUILT  \
44              6,800            1325.0      1930.0   
61              4,000            2001.0      1940.0   
78              3,500            2043.0      1925.0   
108             4,000            2680.0      1899.0   
111             1,710            1872.0      1940.0   

     TAX_CLASS_AT_TIME_OF_SALE  BUILDING_CLASS_AT_TIME_OF_SALE SALE_PRICE  \
44                           1                              A9     550000   
61                           1                              A1     200000   
78                           1                              A1     810000   
108                          1                              A1     125000   
111                          1                              A5     620000   

      SALE_DATE  
44   01/01/2019  
61   01/01/2019  
78   01/02/2019  
108  01/02/2019  
111  01/02/2019  

[5 rows x 21 columns]

In [9]:
data.describe()

BLOCK          LOT  EASE-MENT      ZIP_CODE  RESIDENTIAL_UNITS  \
count   3151.000000  3151.000000        0.0   3151.000000        3151.000000   
mean    6917.976515    75.981593        NaN  11027.219613           0.987623   
std     3963.326705   161.089514        NaN    482.875284           0.113414   
min       21.000000     1.000000        NaN  10030.000000           0.000000   
25%     4016.000000    21.000000        NaN  10461.000000           1.000000   
50%     6301.000000    42.000000        NaN  11235.000000           1.000000   
75%    10208.500000    69.000000        NaN  11413.000000           1.000000   
max    16350.000000  2720.000000        NaN  11697.000000           2.000000   

       COMMERCIAL_UNITS  TOTAL_UNITS  GROSS_SQUARE_FEET   YEAR_BUILT  \
count       3151.000000  3151.000000        3151.000000  3151.000000   
mean           0.015868     1.003491        1470.306887  1943.694700   
std            0.127499     0.171789         586.339200    26.676786   
min            0.000000     0.000000           0.000000  1890.000000   
25%            0.000000     1.000000        1144.000000  1925.000000   
50%            0.000000     1.000000        1360.000000  1938.000000   
75%            0.000000     1.000000        1683.000000  1955.000000   
max            2.000000     3.000000        7875.000000  2018.000000   

       TAX_CLASS_AT_TIME_OF_SALE    SALE_PRICE  
count                     3151.0  3.151000e+03  
mean                         1.0  6.285601e+05  
std                          0.0  2.929904e+05  
min                          1.0  1.040000e+05  
25%                          1.0  4.475000e+05  
50%                          1.0  5.680000e+05  
75%                          1.0  7.600000e+05  
max                          1.0  1.955000e+06

In [10]:
data.describe(exclude="number")

BOROUGH NEIGHBORHOOD  BUILDING_CLASS_CATEGORY TAX_CLASS_AT_PRESENT  \
count     3151         3151                     3151                 3151   
unique       5            7                        1                    2   
top          4        OTHER  01 ONE FAMILY DWELLINGS                    1   
freq      1580         2959                     3151                 3111   

       BUILDING_CLASS_AT_PRESENT             ADDRESS APARTMENT_NUMBER  \
count                       3151                3151                1   
unique                        13                3135                1   
top                           A1  57 CHESTNUT STREET              RP.   
freq                        1185                   2                1   

       LAND_SQUARE_FEET BUILDING_CLASS_AT_TIME_OF_SALE   SALE_DATE  
count              3151                           3151        3151  
unique             1035                             11          91  
top               4,000                             A1  01/31/2019  
freq                289                           1186          78

In [11]:
from pandas_profiling import ProfileReport
PR = ProfileReport(data, minimal=True)
PR.to_notebook_iframe()

In [12]:
data["EASE-MENT"]

44      NaN
61      NaN
78      NaN
108     NaN
111     NaN
         ..
23029   NaN
23031   NaN
23032   NaN
23033   NaN
23035   NaN
Name: EASE-MENT, Length: 3151, dtype: float64

In [13]:
data = data.drop(["BUILDING_CLASS_AT_PRESENT", "BUILDING_CLASS_CATEGORY", "ADDRESS", "APARTMENT_NUMBER", "LAND_SQUARE_FEET",
             "BUILDING_CLASS_AT_TIME_OF_SALE", "EASE-MENT", "TAX_CLASS_AT_TIME_OF_SALE"], axis=1)

In [14]:
print(data.shape)
data.head()

(3151, 13)


BOROUGH NEIGHBORHOOD TAX_CLASS_AT_PRESENT  BLOCK  LOT  ZIP_CODE  \
44        3        OTHER                    1   5495  801   11230.0   
61        4        OTHER                    1   7918   72   11427.0   
78        2        OTHER                    1   4210   19   10461.0   
108       3        OTHER                    1   5212   69   11226.0   
111       3        OTHER                    1   7930  121   11203.0   

     RESIDENTIAL_UNITS  COMMERCIAL_UNITS  TOTAL_UNITS  GROSS_SQUARE_FEET  \
44                 1.0               0.0          1.0             1325.0   
61                 1.0               0.0          1.0             2001.0   
78                 1.0               0.0          1.0             2043.0   
108                1.0               0.0          1.0             2680.0   
111                1.0               0.0          1.0             1872.0   

     YEAR_BUILT  SALE_PRICE   SALE_DATE  
44       1930.0      550000  01/01/2019  
61       1940.0      200000  01/01/2019  
78       1925.0      810000  01/02/2019  
108      1899.0      125000  01/02/2019  
111      1940.0      620000  01/02/2019

In [15]:
data["SALE_DATE"] = pd.to_datetime(df["SALE_DATE"], infer_datetime_format=True)

In [16]:
data["SALE_DATE"].head()

44    2019-01-01
61    2019-01-01
78    2019-01-02
108   2019-01-02
111   2019-01-02
Name: SALE_DATE, dtype: datetime64[ns]

In [17]:
cutoff = pd.to_datetime('2019-04-01')
train = data[data["SALE_DATE"] < cutoff]
test = data[data["SALE_DATE"] >= cutoff]

In [18]:
y_train = train["SALE_PRICE"]
y_test = test["SALE_PRICE"]
X_train = train.drop(["SALE_PRICE", "SALE_DATE"], axis=1)
X_test = test.drop(["SALE_PRICE", "SALE_DATE"], axis=1)

In [19]:
y_train.mean()

621573.7423214999

**The code below is not my own; I am simply experimenting with different ways to One Hot Encode.**

In [20]:
from numpy import array
from numpy import argmax
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import OneHotEncoder
# define example
data = ['cold', 'cold', 'warm', 'cold', 'hot', 'hot', 'warm', 'cold', 'warm', 'hot']
values = array(data)
print(values)
# integer encode
label_encoder = LabelEncoder()
integer_encoded = label_encoder.fit_transform(values)
print(integer_encoded)
# binary encode
onehot_encoder = OneHotEncoder(sparse=False)
integer_encoded = integer_encoded.reshape(len(integer_encoded), 1)
onehot_encoded = onehot_encoder.fit_transform(integer_encoded)
print(onehot_encoded)
# invert first example
inverted = label_encoder.inverse_transform([argmax(onehot_encoded[0, :])])
print(inverted)

['cold' 'cold' 'warm' 'cold' 'hot' 'hot' 'warm' 'cold' 'warm' 'hot']
[0 0 2 0 1 1 2 0 2 1]
[[1. 0. 0.]
 [1. 0. 0.]
 [0. 0. 1.]
 [1. 0. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 0. 1.]
 [1. 0. 0.]
 [0. 0. 1.]
 [0. 1. 0.]]
['cold']


In [21]:
profile = ProfileReport(X_train, explorative=True)
profile.to_notebook_iframe()

In [22]:
print(X_train.shape)
X_train

(2507, 11)


BOROUGH NEIGHBORHOOD TAX_CLASS_AT_PRESENT  BLOCK  LOT  ZIP_CODE  \
44          3        OTHER                    1   5495  801   11230.0   
61          4        OTHER                    1   7918   72   11427.0   
78          2        OTHER                    1   4210   19   10461.0   
108         3        OTHER                    1   5212   69   11226.0   
111         3        OTHER                    1   7930  121   11203.0   
...       ...          ...                  ...    ...  ...       ...   
18129       5        OTHER                    1   4081   44   10306.0   
18130       5        OTHER                    1   2373  201   10314.0   
18132       5        OTHER                    1   1132   42   10302.0   
18134       5        OTHER                    1   3395   37   10305.0   
18147       4        OTHER                    1  11159   11   11429.0   

       RESIDENTIAL_UNITS  COMMERCIAL_UNITS  TOTAL_UNITS  GROSS_SQUARE_FEET  \
44                   1.0               0.0          1.0             1325.0   
61                   1.0               0.0          1.0             2001.0   
78                   1.0               0.0          1.0             2043.0   
108                  1.0               0.0          1.0             2680.0   
111                  1.0               0.0          1.0             1872.0   
...                  ...               ...          ...                ...   
18129                1.0               0.0          1.0              921.0   
18130                1.0               0.0          1.0             2128.0   
18132                1.0               0.0          1.0             1807.0   
18134                1.0               0.0          1.0              621.0   
18147                1.0               0.0          1.0             1163.0   

       YEAR_BUILT  
44         1930.0  
61         1940.0  
78         1925.0  
108        1899.0  
111        1940.0  
...           ...  
18129      1950.0  
18130      1980.0  
18132      2018.0  
18134      1930.0  
18147      1950.0  

[2507 rows x 11 columns]

In [23]:
import category_encoders as ce

In [24]:
encode = ce.OneHotEncoder(cols=["TAX_CLASS_AT_PRESENT", "BOROUGH", "NEIGHBORHOOD",
                      "COMMERCIAL_UNITS", "TOTAL_UNITS"], return_df=True,
                 use_cat_names=True)

In [25]:
f_t = encode.fit_transform(X_train, y_train)
FT_test = encode.transform(X_test)

In [26]:
print(f_t.shape)
f_t.head()

(2507, 27)


BOROUGH_3  BOROUGH_4  BOROUGH_2  BOROUGH_5  BOROUGH_1  \
44           1          0          0          0          0   
61           0          1          0          0          0   
78           0          0          1          0          0   
108          1          0          0          0          0   
111          1          0          0          0          0   

     NEIGHBORHOOD_OTHER  NEIGHBORHOOD_FLUSHING-NORTH  \
44                    1                            0   
61                    1                            0   
78                    1                            0   
108                   1                            0   
111                   1                            0   

     NEIGHBORHOOD_EAST NEW YORK  NEIGHBORHOOD_BEDFORD STUYVESANT  \
44                            0                                0   
61                            0                                0   
78                            0                                0   
108                           0                                0   
111                           0                                0   

     NEIGHBORHOOD_FOREST HILLS  ...  RESIDENTIAL_UNITS  COMMERCIAL_UNITS_0.0  \
44                           0  ...                1.0                     1   
61                           0  ...                1.0                     1   
78                           0  ...                1.0                     1   
108                          0  ...                1.0                     1   
111                          0  ...                1.0                     1   

     COMMERCIAL_UNITS_1.0  COMMERCIAL_UNITS_2.0  TOTAL_UNITS_1.0  \
44                      0                     0                1   
61                      0                     0                1   
78                      0                     0                1   
108                     0                     0                1   
111                     0                     0                1   

     TOTAL_UNITS_2.0  TOTAL_UNITS_0.0  TOTAL_UNITS_3.0  GROSS_SQUARE_FEET  \
44                 0                0                0             1325.0   
61                 0                0                0             2001.0   
78                 0                0                0             2043.0   
108                0                0                0             2680.0   
111                0                0                0             1872.0   

     YEAR_BUILT  
44       1930.0  
61       1940.0  
78       1925.0  
108      1899.0  
111      1940.0  

[5 rows x 27 columns]

**With the data encoded above, the cells below are used to fit a predictive model.**

In [27]:
features = f_t.columns
n = len(features)
n

27

In [44]:
from math import factorial

def n_choose_k(n, k):
    return factorial(n)/(factorial(k)*factorial(n-k))

combinations = sum(n_choose_k(n,k) for k in range(1,n+1))
print(combinations)

134217727.0


In [45]:
from sklearn.feature_selection import SelectKBest
selector = SelectKBest(k=15)
X_train_choice = selector.fit_transform(f_t, y_train)
X_test_choice = selector.transform(FT_test)

C:\Users\whyse\anaconda3\envs\unit2\lib\site-packages\sklearn\feature_selection\_univariate_selection.py:116: RuntimeWarning: divide by zero encountered in true_divide
  f = msb / msw


In [46]:
f_t.shape

(2507, 27)

In [47]:
X_train_choice.shape

(2507, 15)

In [57]:
from sklearn.linear_model import Ridge
import numpy as np

ridge = Ridge(alpha=0.5)
ridge.fit(X_train_choice, y_train)

Ridge(alpha=0.5)

In [58]:
ridge.predict(X_test_choice)

array([ 673732.28240088,  364312.34778686,  809126.63392996,
        651365.28112849,  493998.20301706,  634579.16804195,
        583470.41527829,  659112.60419499,  662577.96898247,
        726347.23742953,  655708.92727934,  459423.66866854,
        441158.88346343,  767216.6513218 ,  601304.19114151,
        735164.37961206,  600076.69393012, 1242653.66882645,
        514036.72371683,  657416.87432097, 1251546.22970038,
        570650.81783884,  743595.35967274,  573813.92625264,
        722769.62378921,  559710.32145207,  560173.06767393,
        972474.95356427,  616081.33964901,  653779.63470472,
        580413.64075637,  600113.3940155 ,  587182.10160059,
        453546.54478613,  923330.59491315,  751541.03910192,
        658350.52160443,  577279.77624099,  558275.70543683,
        483848.64120487,  408833.93333383,  460924.16062189,
       1144129.83616397,  605045.62494176,  693708.06225746,
        620595.36085882,  913335.43387864,  581187.08467188,
        527991.21765945,

In [59]:
ridge.score(X_test_choice, y_test)

0.28522754152023677

*The score above is the highest $r^2$ score I could determine.*